In [1]:
require 'apascal-dataset'
require 'loadcaffe'
require 'cutorch'
require 'logger'
require 'image'

-- opt = lapp[[
--       --device          (default 1)        Gpu Device to use
--       --batchSize       (default 10)      Sub-batch size
--       --dataRoot        (default ./dataset/attribute/attribute_data/)        Data root folder
--       --imageRoot       (default ./dataset/attribute/apascal_images/)       Image dir
--       --experimentName  (default "snapshots/svm/")
-- ]]
opt = {}
opt['device']=1
opt['batchSize']=10
opt['dataRoot']='./dataset/attribute/attribute_data/'
opt['imageRoot']='./dataset/attribute/apascal_images/'
opt['experimentName']='snapshots/svm/'

torch.setdefaulttensortype('torch.FloatTensor')
torch.manualSeed(1)

cutorch.setDevice(opt.device)
cutorch.manualSeedAll(1)

model = loadcaffe.load('caffe_models/VGG_ILSVRC_19_layers_deploy.prototxt'
                       ,'caffe_models/VGG_ILSVRC_19_layers.caffemodel'
                       , 'cudnn')
mean = torch.Tensor(1,3,224,224):float()
mean:sub(1,1,1,1):fill(103.939)
mean:sub(1,1,2,2):fill(116.779)
mean:sub(1,1,3,3):fill(123.68)

logger = Logger()
if( opt.loadFrom ~= "" ) then
    logger:open( opt.experimentName, true )
else
    logger:open( opt.experimentName, false )
end
logger:info( opt )

dataset = Dataset( opt.dataRoot,
                   opt.imageRoot,
                   torch.Tensor({0.0,0,0,0,0}),1.0
                   ,opt.batchSize )
train_size, val_size = dataset:size()

balance_weights = {}
local txt = io.open('dataset/attribute/attribute_data/balancing_weights.txt')
for line in txt:lines() do
    line = line:split('\t')
    balance_weights[#balance_weights+1] = {pl = tonumber(line[1]), nl = tonumber(line[2])}
end
txt:close()

Successfully loaded caffe_models/VGG_ILSVRC_19_layers.caffemodel


conv1_1: 64 3 3 3
conv1_2: 64 64 3 3


conv2_1: 128 64 3 3
conv2_2: 128 128 3 3
conv3_1: 256 128 3 3


conv3_2: 256 256 3 3


conv3_3: 256 256 3 3


...

conv5_4: 512 512 3 3


fc6: 1 1 25088 4096


fc7: 1 1 4096 4096


fc8: 1 1 4096 1000


{
  dataRoot : ./dataset/attribute/attribute_data/
  experimentName : snapshots/svm/
  device : 1
  imageRoot : ./dataset/attribute/apascal_images/
  batchSize : 10
}


In [ ]:
local co = dataset:get_train_sample_co()
train_num, valid_num = dataset:size()
features = torch.Tensor(train_num,4096):float()
index = 1

while true do
    flag,ims,labels = coroutine.resume(co,dataset)
    if( ims == nil ) then
        break
    end
    
    processed = ims*255 - torch.expand(mean,ims:size()[1],3,224,224)
    
    collectgarbage();collectgarbage();
    ret = model:forward(processed:cuda())
    
    features:sub(index,index + ims:size()[1]-1):copy(model['modules'][40].output:float()) --FC7 features
    index = index + ims:size()
    
    xlua.progress(train_num,index)
end

In [1]:
features = torch.load('snapshots/svm/fc7-features.th')
labels = torch.load('snapshots/svm/labels.th')

for i = 1, 6340 do --train_num
    local t = {}
    if( labels[1][i] == 0 ) then
        table.insert(t,'-1 ')
    else
        table.insert(t,'+1 ')
    end 
    for j = 1,4096 do
        table.insert(t,tostring(j)..':'..tostring(features[i][j])..' ')
    end
    print (table.concat(t,''))
end

    
-- print (features:size())
-- print (features[6340])
-- print (torch.nonzero(labels[1]):size())

-1 1:0 2:0 3:0 4:0 5:0 6:0 7:0 8:0 9:0 10:0 11:0 12:0 13:0 14:0 15:0 16:0 17:3.4731929302216 18:0 19:0 20:0 21:0 22:1.0728981494904 23:0 24:0 25:0 26:0 27:0 28:0 29:0 30:0 31:16.40870475769 32:8.0397481918335 33:0 34:0 35:0 36:0 37:0 38:0 39:22.809270858765 40:0 41:0 42:0 43:0 44:0 45:0 46:0 47:0 48:6.0243167877197 49:0 50:0 51:0 52:0 53:20.581447601318 54:0.46581968665123 55:0 56:0 57:0 58:0 59:0 60:0 61:0 62:0 63:0 64:0 65:6.9531717300415 66:0 67:10.311560630798 68:10.893510818481 69:0.081639856100082 70:0 71:0 72:0 73:0 74:0 75:0 76:0 77:0 78:6.3080077171326 79:0 80:0 81:0 82:0 83:0 84:0.92903745174408 85:0 86:0 87:0 88:0 89:0 90:0 91:0 92:0 93:0 94:0 95:0 96:0 97:5.9853940010071 98:0 99:0 100:0 101:0 102:0 103:0 104:0 105:0 106:0 107:0 108:0 109:0 110:0 111:8.0889520645142 112:2.8893129825592 113:0 114:0 115:0 116:0 117:0 118:0 119:0 120:0 121:0 122:0 123:0 124:3.0152974128723 125:0 126:0 127:0 128:0 129:0 130:0 131:0 132:0 133:4.9347405433655 134:0 135:5.0053596496582 136:0 137:0 

2:0 493:2.5628550052643 494:0 495:0 496:0 497:3.2878048419952 498:0 499:0 500:0 501:0 502:0 503:0 504:0 505:0 506:0 507:0 508:0 509:0 510:0 511:1.449543595314 512:0 513:5.3350429534912 514:0 515:0 516:0 517:2.7520337104797 518:0 519:0 520:0 521:0 522:0 523:0 524:0 525:0 526:0 527:0 528:0 529:0 530:0 531:0 532:0 533:0 534:0 535:0 536:0 537:0 538:0 539:0 540:0 541:0 542:1.4670544862747 543:0 544:0 545:0.75479769706726 546:1.098372220993 547:0 548:0 549:0 550:0 551:7.2732791900635 552:4.4890851974487 553:0 554:0 555:0 556:18.336654663086 557:0 558:0 559:0 560:0 561:0 562:0 563:0 564:0 565:0 566:0 567:0 568:0.19393031299114 569:0 570:0 571:2.3047215938568 572:0 573:0 574:0 575:0 576:0 577:0 578:4.1639790534973 579:0 580:8.4018602371216 581:3.8437125682831 582:4.3197913169861 583:0 584:0.10674014687538 585:8.4070196151733 586:0 587:0 588:0 589:0 590:0 591:0 592:0 593:16.888063430786 594:0 595:2.8428044319153 596:0 597:0 598:0.24081914126873 599:2.6819131374359 600:2.0077297687531 601:0 602:

7:4.7406764030457 938:0 939:0 940:0 941:0 942:0 943:0 944:20.515308380127 945:0 946:0 947:0 948:0 949:22.11424446106 950:0 951:21.230171203613 952:3.0758163928986 953:0 954:0 955:0 956:19.137105941772 957:5.9316992759705 958:0 959:22.79712677002 960:0 961:0 962:0 963:0 964:0 965:0 966:0 967:0 968:2.6180517673492 969:0 970:0 971:3.9726028442383 972:0 973:5.7271943092346 974:0 975:0 976:0 977:3.2469906806946 978:0 979:0 980:0 981:0 982:0 983:0 984:0 985:0 986:0.63712406158447 987:0 988:0 989:0 990:0 991:0 992:15.237457275391 993:8.4199094772339 994:0 995:0 996:0 997:0 998:0 999:4.2973699569702 1000:0 1001:0 1002:0 1003:10.285742759705 1004:2.4323992729187 1005:0 1006:0 1007:0 1008:4.2896342277527 1009:0 1010:6.2367486953735 1011:0 1012:0 1013:0 1014:0 1015:0 1016:0 1017:0 1018:0 1019:0 1020:0 1021:0 1022:0 1023:0 1024:0 1025:6.3021850585938 1026:0 1027:0.94921272993088 1028:6.9925427436829 1029:0 1030:0 1031:8.6535701751709 1032:0.21161845326424 1033:0 1034:0 1035:0 1036:10.335357666016 

56:15.04258441925 1357:0 1358:0 1359:0 1360:0 1361:0 1362:2.0027523040771 1363:0 1364:0 1365:0 1366:0 1367:0 1368:0 1369:8.0002813339233 1370:3.4978189468384 1371:0 1372:0 1373:0 1374:0 1375:0 1376:10.798830986023 1377:0 1378:0 1379:4.6784129142761 1380:0 1381:0 1382:0 1383:0 1384:0.79944270849228 1385:9.3022165298462 1386:0.65668553113937 1387:0 1388:0 1389:7.5740556716919 1390:0 1391:3.4479076862335 1392:0 1393:0 1394:10.260610580444 1395:0 1396:0 1397:0 1398:0 1399:15.665567398071 1400:0 1401:0 1402:0 1403:0 1404:0 1405:0 1406:0 1407:0 1408:0 1409:0 1410:0 1411:0 1412:5.0243735313416 1413:0 1414:0 1415:0 1416:0 1417:0 1418:0 1419:0 1420:4.5830526351929 1421:0 1422:0 1423:3.7796227931976 1424:0 1425:0 1426:0 1427:0 1428:0 1429:0.75432187318802 1430:0 1431:0 1432:0 1433:0 1434:0.58047497272491 1435:0 1436:0 1437:0 1438:0 1439:0 1440:0 1441:0 1442:12.767028808594 1443:0 1444:0 1445:0 1446:0 1447:0 1448:3.7860023975372 1449:0 1450:0 1451:0 1452:0.86193406581879 1453:0 1454:0 1455:0 1456

7771 1769:0 1770:0 1771:0 1772:0 1773:0 1774:1.2574956417084 1775:0 1776:0 1777:5.3880486488342 1778:0 1779:9.8928232192993 1780:0 1781:0 1782:1.5075968503952 1783:0 1784:0 1785:6.3365588188171 1786:6.1941685676575 1787:0 1788:0 1789:0 1790:0 1791:0 1792:0 1793:0 1794:0.56850719451904 1795:5.236074924469 1796:0 1797:0 1798:4.354944229126 1799:0 1800:0 1801:18.057685852051 1802:0 1803:0 1804:0 1805:0.75597059726715 1806:0 1807:0 1808:0 1809:0 1810:9.9750995635986 1811:4.861231803894 1812:0 1813:16.297689437866 1814:0 1815:0 1816:0 1817:0 1818:0 1819:4.4689788818359 1820:0 1821:0 1822:9.2792711257935 1823:0 1824:0 1825:0 1826:0 1827:0 1828:0 1829:0 1830:0 1831:0 1832:7.903573513031 1833:2.3944067955017 1834:0 1835:3.6424338817596 1836:0 1837:1.7475669384003 1838:0 1839:0 1840:17.523813247681 1841:0 1842:0 1843:0 1844:0 1845:0 1846:0 1847:0 1848:0 1849:0 1850:0 1851:0 1852:0 1853:0 1854:0 1855:4.3971543312073 1856:0 1857:0 1858:0 1859:0 1860:1.8248189687729 1861:0 1862:0.7540767788887 186

...

81:0 2082:0 2083:0 2084:0 2085:0 2086:0 2087:0 2088:0 2089:0 2090:0 2091:6.9512324333191 2092:0 2093:0.54436856508255 2094:0 2095:0 2096:4.881630897522 2097:0 2098:0 2099:4.5969533920288 2100:0 2101:0 2102:0 2103:6.1886615753174 2104:0 2105:0 2106:0 2107:0 2108:0 2109:1.3336002826691 2110:0 2111:0 2112:0 2113:0 2114:1.5917749404907 2115:0 2116:8.2268648147583 2117:0 2118:0 2119:0 2120:0 2121:0 2122:0 2123:0 2124:0 2125:0 2126:0 2127:0 2128:11.146039962769 2129:4.6672525405884 2130:0 2131:0 2132:0 2133:0 2134:0 2135:0 2136:0 2137:0 2138:1.3631954193115 2139:0 2140:0 2141:2.0554597377777 2142:0 2143:0 2144:0 2145:0 2146:0 2147:0 2148:0 2149:0 2150:0 2151:0 2152:0 2153:0 2154:0 2155:0 2156:0 2157:0 2158:0 2159:0 2160:0 2161:0 2162:0.50297325849533 2163:0 2164:8.0428676605225 2165:1.2124892473221 2166:0 2167:0 2168:0 2169:0.15849176049232 2170:5.6434001922607 2171:0 2172:0 2173:2.9687485694885 2174:0 2175:0 2176:0 2177:0 2178:0 2179:10.690576553345 2180:0 2181:0 2182:0 2183:5.8831901550293

:0 2503:1.1862305402756 2504:0 2505:7.046543598175 2506:0 2507:5.4832787513733 2508:0 2509:0 2510:0 2511:0 2512:0 2513:4.8870730400085 2514:0 2515:0 2516:4.8942809104919 2517:0.37197640538216 2518:4.1423382759094 2519:0 2520:0 2521:0 2522:13.157835960388 2523:5.8090467453003 2524:0 2525:0 2526:0 2527:0.063533589243889 2528:0 2529:0 2530:0 2531:9.8245038986206 2532:0 2533:0 2534:0 2535:0 2536:0 2537:0 2538:0 2539:0.45453822612762 2540:0 2541:13.898801803589 2542:0 2543:0 2544:0 2545:0 2546:0 2547:2.3665823936462 2548:0 2549:0 2550:0 2551:0 2552:1.2888324260712 2553:0 2554:0 2555:0 2556:0 2557:0 2558:0 2559:0 2560:0 2561:0 2562:0 2563:16.517055511475 2564:0 2565:0 2566:0 2567:0 2568:12.347431182861 2569:0 2570:0 2571:0 2572:0 2573:1.9159872531891 2574:0 2575:0 2576:0 2577:0 2578:3.4240851402283 2579:0 2580:3.7093677520752 2581:8.9426441192627 2582:0 2583:0 2584:0 2585:0 2586:4.9876623153687 2587:0 2588:0 2589:3.1841368675232 2590:0 2591:0.16869044303894 2592:0 2593:0 2594:0 2595:0 2596:0

3:0 2894:0 2895:0 2896:0 2897:0 2898:0 2899:0 2900:0 2901:0 2902:0 2903:0 2904:0 2905:0 2906:0 2907:2.8751876354218 2908:0 2909:0 2910:0.62963688373566 2911:0 2912:0 2913:0 2914:0 2915:0 2916:0 2917:3.2627894878387 2918:0 2919:2.3183643817902 2920:0 2921:0 2922:0 2923:0 2924:0 2925:0 2926:0 2927:0 2928:0 2929:0 2930:0 2931:0 2932:0.58675140142441 2933:0 2934:0.4070905148983 2935:0 2936:0 2937:0 2938:0 2939:0 2940:0 2941:0.070993661880493 2942:0 2943:0 2944:8.982684135437 2945:0 2946:0 2947:0 2948:0 2949:8.1162815093994 2950:0 2951:0 2952:1.7451093196869 2953:0 2954:0 2955:0 2956:0 2957:0 2958:0 2959:0 2960:10.986471176147 2961:0 2962:0 2963:0 2964:0 2965:0.12588229775429 2966:3.6503255367279 2967:0 2968:0 2969:0 2970:0 2971:0 2972:0.9259774684906 2973:0 2974:0 2975:0 2976:0 2977:0 2978:0 2979:1.7641421556473 2980:0 2981:0 2982:0.2147935628891 2983:0 2984:0 2985:0 2986:0 2987:1.0575597286224 2988:0 2989:0 2990:0 2991:0 2992:4.7633056640625 2993:0 2994:0 2995:0 2996:0 2997:0 2998:0 2999:

08:0 3309:0 3310:0 3311:0 3312:0 3313:3.408203125 3314:0 3315:7.6488227844238 3316:0 3317:3.7940554618835 3318:0 3319:0 3320:9.9082508087158 3321:0 3322:0 3323:0.37842482328415 3324:1.1470313072205 3325:0 3326:0 3327:0 3328:0 3329:4.5375757217407 3330:4.7022285461426 3331:0 3332:0 3333:0 3334:0 3335:0 3336:0 3337:0 3338:0 3339:0 3340:6.5463151931763 3341:7.6939263343811 3342:0 3343:0 3344:0 3345:0 3346:0 3347:16.530839920044 3348:0 3349:0 3350:4.0744681358337 3351:0 3352:0 3353:0 3354:0 3355:0 3356:0 3357:0 3358:3.2240028381348 3359:0 3360:0 3361:0 3362:5.5159502029419 3363:0 3364:0 3365:0.97143161296844 3366:0 3367:0 3368:0 3369:0 3370:0.82384872436523 3371:0 3372:0 3373:0 3374:0 3375:0 3376:0 3377:0 3378:4.589738368988 3379:0 3380:1.2139075994492 3381:0 3382:0 3383:0 3384:0 3385:0 3386:0 3387:0 3388:0 3389:0 3390:0.15200497210026 3391:1.4268015623093 3392:0 3393:0 3394:0 3395:0 3396:4.2133736610413 3397:1.6969374418259 3398:0 3399:0 3400:0 3401:0 3402:0 3403:0 3404:0 3405:0 3406:3.12

0 3726:0 3727:0 3728:0 3729:0 3730:0 3731:0 3732:0 3733:0 3734:0 3735:5.8754496574402 3736:2.6055352687836 3737:0 3738:4.6458644866943 3739:0 3740:0 3741:0 3742:0 3743:3.578182220459 3744:0 3745:0 3746:0 3747:0 3748:0 3749:0 3750:0 3751:0 3752:0 3753:0 3754:0 3755:0 3756:0 3757:0 3758:0 3759:0 3760:0 3761:0 3762:0 3763:0 3764:0 3765:0 3766:5.7372660636902 3767:0 3768:0 3769:0 3770:0 3771:5.4094071388245 3772:0 3773:2.8439650535583 3774:0 3775:0 3776:0 3777:0 3778:0 3779:0 3780:0 3781:0.90965378284454 3782:0 3783:0 3784:0 3785:0 3786:0 3787:5.7436575889587 3788:0 3789:0 3790:0 3791:0 3792:0 3793:0 3794:0 3795:0 3796:0 3797:0 3798:1.6973605155945 3799:0 3800:0 3801:5.8843307495117 3802:0 3803:0 3804:9.2606773376465 3805:1.1520470380783 3806:0 3807:0 3808:0 3809:0 3810:6.2536420822144 3811:0 3812:0 3813:0 3814:0 3815:0 3816:1.7365838289261 3817:0 3818:0 3819:8.1428804397583 3820:0 3821:0 3822:0 3823:0 3824:0 3825:3.7106833457947 3826:7.0093913078308 3827:0 3828:0 3829:0 3830:0 3831:0 3832